In [126]:
###############
####IMPORTS####
###############

import yaml
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.colors as mcolors

from PIL import Image
from io import BytesIO
from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA

In [129]:
####################
####DATA LOADING####
####################

with open("./data/pokemon-forms.yaml", 'r') as file:
    data = yaml.safe_load(file)
data_list = [value for value in data.values()]
df = pd.DataFrame(data_list)

with open('./data/moves.yaml', 'r') as file:
    moves_data = yaml.safe_load(file)
data_list = [value for value in moves_data.values()]
moves_df = pd.DataFrame(data_list)
moves_df['power'] = pd.to_numeric(moves_df['power'], errors='coerce').fillna(0)
moves_df['accuracy'] = pd.to_numeric(moves_df['accuracy'], errors='coerce').fillna(100)
moves_df['pp'] = pd.to_numeric(moves_df['pp'], errors='coerce').fillna(10)

In [134]:
fig = px.scatter_matrix(
    moves_df,
    dimensions=["power", "accuracy", "pp", "priority"],
    color='name'
)
fig.update_traces(diagonal_visible=False)
fig.show()

In [131]:
#selection des variables
features=moves_df[["power", "accuracy", "pp", "priority"]]

#calcul tsne
tsne = TSNE(n_components=2, random_state=0)
projections = tsne.fit_transform(features)

#copie dans le df
moves_df['x'] = projections[:, 0]
moves_df['y'] = projections[:, 1]

fig = px.scatter(
    moves_df,
    x='x', 
    y='y',
    color='category', 
    hover_name='name',
    hover_data=['type', 'power', 'accuracy', 'pp', 'category'],
    labels={'x': 't-SNE 1', 'y': 't-SNE 2'}
)
fig.show()

In [182]:
###############
####LIBRARY####
###############
import requests

def get_pokemon_image(pokemon_id):
    url = f"https://img.pokemondb.net/artwork/large/{pokemon_id}.jpg"
    
    try:
        response = requests.get(url)
        response.raise_for_status() # checks for errors
        
        return response.content
    
    except requests.RequestException as e:
        print(f"Error downloading image: {e}")
        
#inutile pour l'instant
def get_min_max(stat):
    temp = 0
    id = 0
    i = 0
    for index, row in df.iterrows():
        if row['stats'][stat] > temp:
            temp = row['stats'][stat]
            id = i
        i += 1
    return id
get_min_max('spdef')

1058

In [168]:
#################
####VARIABLES####
#################

type_link = {
    "normal": "https://archives.bulbagarden.net/media/upload/thumb/0/08/NormalIC_SV.png/105px-NormalIC_SV.png",
    "fighting": "https://archives.bulbagarden.net/media/upload/thumb/0/0f/FightingIC_SV.png/105px-FightingIC_SV.png",
    "flying": "https://archives.bulbagarden.net/media/upload/thumb/d/d7/FlyingIC_SV.png/105px-FlyingIC_SV.png",
    "poison": "https://archives.bulbagarden.net/media/upload/thumb/9/9d/PoisonIC_SV.png/105px-PoisonIC_SV.png",
    "ground": "https://archives.bulbagarden.net/media/upload/thumb/f/f8/GroundIC_SV.png/105px-GroundIC_SV.png",
    "rock": "https://archives.bulbagarden.net/media/upload/thumb/3/32/RockIC_SV.png/105px-RockIC_SV.png",
    "bug": "https://archives.bulbagarden.net/media/upload/thumb/d/d1/BugIC_SV.png/105px-BugIC_SV.png",
    "ghost": "https://archives.bulbagarden.net/media/upload/thumb/2/2c/GhostIC_SV.png/105px-GhostIC_SV.png",
    "steel": "https://archives.bulbagarden.net/media/upload/thumb/b/b8/SteelIC_SV.png/105px-SteelIC_SV.png",
    "fire": "https://archives.bulbagarden.net/media/upload/thumb/a/a2/FireIC_SV.png/105px-FireIC_SV.png",
    "water": "https://archives.bulbagarden.net/media/upload/thumb/d/de/WaterIC_SV.png/105px-WaterIC_SV.png",
    "grass": "https://archives.bulbagarden.net/media/upload/thumb/7/7b/GrassIC_SV.png/105px-GrassIC_SV.png",
    "electric": "https://archives.bulbagarden.net/media/upload/thumb/7/77/ElectricIC_SV.png/105px-ElectricIC_SV.png",
    "psychic": "https://archives.bulbagarden.net/media/upload/thumb/1/13/IceIC_SV.png/105px-IceIC_SV.png",
    "ice": "https://archives.bulbagarden.net/media/upload/thumb/9/96/PsychicIC_SV.png/105px-PsychicIC_SV.png",
    "dragon": "https://archives.bulbagarden.net/media/upload/thumb/7/7f/DragonIC_SV.png/105px-DragonIC_SV.png",
    "dark": "https://archives.bulbagarden.net/media/upload/thumb/3/30/DarkIC_SV.png/105px-DarkIC_SV.png",
    "fairy": "https://archives.bulbagarden.net/media/upload/thumb/c/c6/FairyIC_SV.png/105px-FairyIC_SV.png"
}
stat_names = {
    'hp':'HP',
    'attack':'Attack',
    'defense':'Defense',
    'spatk':'Sp. Atk.',
    'spdef':'Sp. Def.',
    'speed':'Speed'
}

stats_statistics = pd.DataFrame(df['stats'])['stats'].apply(pd.Series).describe().round(2).to_dict()

stat_colormap = mcolors.LinearSegmentedColormap.from_list("pokemon_stat", ["red", "yellow", "lime"], N=160)

In [204]:
#########################
##POKEMON DISPLAY RADAR##
#########################

pokemon = df.iloc[6]

fig = go.Figure()

fig.add_trace(go.Scatterpolar(
    r=list(pokemon['stats'].values()),
    theta=list(pokemon['stats'].keys()),
    fill='toself',
    name=pokemon['pokemonid'],
    opacity=0.5
))
fig.update_layout(polar=dict(domain=dict(x=[0.7, 1],y=[0, 1])))

fig.add_annotation(
    x=0.45, y=0.8,
    text=f"{pokemon['pokemonid'].upper()}",
    showarrow=False,
    font=dict(
        size=36,
        family="Courier New",  # Changes font family
        color='Black'    # Changes text color
    )
)

fig.add_layout_image(
    dict(
        source=Image.open(BytesIO(get_pokemon_image(pokemon['pokemonid']))),
        x=0.1, y=0.5, sizex=0.3, sizey=1,
        xanchor='center', yanchor='middle'
    )
)

fig.add_layout_image(
    dict(
        source=Image.open(BytesIO(requests.get(type_link[pokemon['type1']]).content)),
        x=0.45, y=0.6, sizex=0.15, sizey=1,
        xanchor='center', yanchor='middle'
    )
)

if pokemon['type2'] is not None:
    fig.add_layout_image(
        dict(
            source=Image.open(BytesIO(requests.get(type_link[pokemon['type2']]).content)),
            x=0.45, y=0.5, sizex=0.15, sizey=1,
            xanchor='center', yanchor='middle'
        )
    )
fig.show()
#print(".")#don't show the plot for space

In [190]:
pokemon

pokemonid                                               venusaur
formid                                                      None
formname                                                    None
gen                                                            1
release                                                 red-blue
type1                                                      grass
type2                                                     poison
stats          {'hp': 80, 'attack': 82, 'defense': 83, 'spatk...
species                                                     Seed
height                                                       2.0
weight                                                     100.0
gender                                                       1:7
catch-rate                                                  45.0
base-exp                                                   236.0
egg-cycles                                                  20.0
friendship               

In [6]:
###########################
##POKEMON DISPLAY BARPLOT##
###########################

pokemon = df.iloc[182]
fig = go.Figure()

# barplot
for stat, value in pokemon['stats'].items():
    fig.add_trace(go.Bar(
        y=[f"{stat_names[stat]} "],
        x=[value],
        text=[f"<b>{value}</b>"],
        orientation='h',
        marker_color=mcolors.to_hex(stat_colormap(value)),
        showlegend=False,
        opacity=0.7
    ))

fig.update_layout(
    title=f"{pokemon['pokemonid'].capitalize()}",
    height=300,
    margin=dict(l=200),
    xaxis=dict(
        domain=[0.4, 1],
        range=[0, 255]
    )
)

#Image du pokémon
fig.add_layout_image(
        dict(
            source=Image.open(BytesIO(get_pokemon_image(pokemon['pokemonid']))),
            x=-0.2, y=1,  
            sizex=1,
            sizey=1
        )
    )

In [7]:
#FAIRE UN RESEAU DIRECTIONNEL DES TYPES GENRE LIE QUI BAT QUI avec les faiblessent/résistance etc...

In [8]:
# (faut bien qu'on rende un site avec dash, pas un notebook)